In [17]:
import OpenDartReader
import configparser
import pandas as pd 
import re
import warnings
from bs4 import BeautifulSoup
from tqdm import tqdm

warnings.filterwarnings('ignore')
config = configparser.ConfigParser()
config.read('config.ini', encoding ='utf-8')

['config.ini']

In [3]:
api_key = config['dart']['key']
dart = OpenDartReader(api_key)

In [4]:
report_2020 = pd.read_csv('dataset/report_2020_list.csv')

In [5]:
report_2020

corp_code corp_name  stock_code corp_cls              report_nm  \
0        100601     강원에너지    114190.0        K        사업보고서 (2020.12)   
1        100656      강원일보         NaN        E        사업보고서 (2020.12)   
2        100814     포스코건설         NaN        E        사업보고서 (2020.12)   
3        100939    강남제비스코       860.0        Y        사업보고서 (2020.12)   
4        101044   에이프로젠제약      3060.0        Y        사업보고서 (2020.12)   
...         ...       ...         ...      ...                    ...   
2864    1513431    인동첨단소재         NaN        E  [기재정정]사업보고서 (2020.12)   
2865    1513440    한국9호스팩    368770.0        K        사업보고서 (2020.12)   
2866    1514528   신한제7호스팩    366330.0        K        사업보고서 (2020.12)   
2867    1515323  LG에너지솔루션    373220.0        Y        사업보고서 (2020.12)   
2868    1524507        핀텔         NaN        E  [기재정정]사업보고서 (2020.12)   

            rcept_no    flr_nm  rcept_dt   rm  
0     20210402002033     강원에너지  20210402    연  
1     20210331000666      강원일보  20210331  NaN  
2     20210305000704     포스코건설  20210305    연  
3     20210317000299    강남제비스코  20210317    연  
4     20210318000458   에이프로젠제약  20210318    연  
...              ...       ...       ...  ...  
2864  20210909000369    인동첨단소재  20210910  NaN  
2865  20210319000079    한국9호스팩  20210319  NaN  
2866  20210319000368   신한제7호스팩  20210319  NaN  
2867  20210317000676  LG에너지솔루션  20210317    연  
2868  20211109000077        핀텔  20211109  NaN  

[2869 rows x 9 columns]

In [6]:
report_2020.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2869 entries, 0 to 2868
Data columns (total 9 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   corp_code   2869 non-null   int64  
 1   corp_name   2869 non-null   object 
 2   stock_code  2497 non-null   float64
 3   corp_cls    2869 non-null   object 
 4   report_nm   2869 non-null   object 
 5   rcept_no    2869 non-null   int64  
 6   flr_nm      2869 non-null   object 
 7   rcept_dt    2869 non-null   int64  
 8   rm          2055 non-null   object 
dtypes: float64(1), int64(3), object(5)
memory usage: 201.9+ KB


In [7]:
report_2020['stock_code'] = report_2020['stock_code'].fillna(0).apply(lambda x : str(f'{int(x):0>6}'))

In [8]:
report_2020.corp_code = report_2020.corp_code.astype(str)

In [9]:
report_2020['name_code'] = report_2020.corp_name+'_'+report_2020['corp_code']

In [10]:
report_2020['corp_code'].nunique()

2869

In [11]:
report_2020['name_code'][0]

'강원에너지_100601'

In [18]:
def preprocessing(xml_text):
    soup = BeautifulSoup(xml_text)
    doc_text = soup.get_text()
    
    doc_text = re.sub('[\n-]', '', doc_text)
    doc_text = re.sub('&cr;', '', doc_text)
    
    return doc_text

In [74]:
report_2020.iloc[225:232]

corp_code corp_name stock_code corp_cls              report_nm  \
225    119195      동화약품     000020        Y        사업보고서 (2020.12)   
226    119672        두올     016740        Y  [기재정정]사업보고서 (2020.12)   
227    119724     두원중공업     000000        E        사업보고서 (2020.12)   
228    120021        LG     003550        Y        사업보고서 (2020.12)   
229    120030      GS건설     006360        Y        사업보고서 (2020.12)   
230    120076   LX인터내셔널     001120        Y        사업보고서 (2020.12)   
231    120182    NH투자증권     005940        Y        사업보고서 (2020.12)   

           rcept_no   flr_nm  rcept_dt rm       name_code  
225  20210317000578     동화약품  20210317  연     동화약품_119195  
226  20210322000709       두올  20210322  연       두올_119672  
227  20210331002447    두원중공업  20210331  연    두원중공업_119724  
228  20210311000968       LG  20210311  연       LG_120021  
229  20210318000969     GS건설  20210318  연     GS건설_120030  
230  20210316000546  LX인터내셔널  20210316  연  LX인터내셔널_120076  
231  20210317000233   NH투자증권  20210317  연   NH투자증권_120182

In [72]:
dart.document('20210311000968')

'<?xml version="1.0" encoding="utf-8"?>\r\n\r\n\r\n<DOCUMENT xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:noNamespaceSchemaLocation="dart3.xsd">\n\n<DOCUMENT-HEADER AEXT-CLASS="Y">\n<DOCUMENT-NAME ACODE="11011">사업보고서</DOCUMENT-NAME>\n<FORMULA-VERSION SUBVER="1" ADATE="20210122">4.2</FORMULA-VERSION>\n<COMPANY-NAME AREGCIK="00120021">(주)LG</COMPANY-NAME>\n\n<SUMMARY>\n<EXTRACTION ACODE="LINK_FLAG" AFEATURE="BOTH">C</EXTRACTION>\n<EXTRACTION ACODE="FIN_TYPE" AFEATURE="BOTH">A</EXTRACTION>\n<EXTRACTION ACODE="CRP_RGS_NO_TEMP" AFEATURE="BOTH">110111-0003543</EXTRACTION>\n</SUMMARY>\n</DOCUMENT-HEADER>\n\n<BODY>\n\n<INSERTION ABASISNUMBER="SE1" AFREQUENCY="0" ADUPLICATION="N">\n<COMMENT>◆click◆ 정정문서 작성시 『정오표』 삽입</COMMENT>\n<LIBRARYLIST>정정신고(보고)-대표이사등의확인.LCommon</LIBRARYLIST>\n</INSERTION>\n\n<COVER>\n<P></P>\n<COVER-TITLE ATOC="Y" AASSOCNOTE="COVER">사 업 보 고 서</COVER-TITLE>\n<P>&cr;&cr;&cr;</P>\n<P USERMARK="F-16">                                    (제 59 기)</P>\n\n<TABLE-GROUP 

In [76]:
with open('report_2020.txt', 'w') as f:
    f.write('')

In [77]:
list_comp = []
for i, v in tqdm(enumerate(report_2020.corp_code)):
    doc_num = report_2020.rcept_no[i]
    
    try:
        xml_text = dart.document(doc_num)
        with open('report_2020.txt', 'a') as f:
            f.write(report_2020['corp_code'][i]) 
            f.write('\t')
            f.write(preprocessing(xml_text))
            f.write('\n')
        
    except: 
        print(i,v)
        list_comp.append(v)
    

449it [05:20,  1.09s/it]

448 137997


700it [10:06,  1.27s/it]

699 160010


995it [15:49,  1.63s/it]

...

2528it [1:06:43, 381.85s/it]

2527 1139497


2585it [1:07:59,  1.04s/it] 

2584 1186963


2869it [1:11:01,  1.49s/it]


In [1]:
list_comp = ['137997','160010','234227','269940','415594','501970','528515','819268','1096341','1113718','1139497','1186963']

In [14]:
temp = report_2020[report_2020.corp_code.isin(list_comp)]

In [23]:
temp = temp.reset_index().drop('index', axis =1)

In [24]:
list_comp = []
for i, v in tqdm(enumerate(temp.corp_code)):
    doc_num = temp.rcept_no[i]
    
    try:
        xml_text = dart.document(doc_num)
        with open('report_2020.txt', 'a') as f:
            f.write(temp['corp_code'][i]) 
            f.write('\t')
            f.write(preprocessing(xml_text))
            f.write('\n')
        
    except: 
        print(i,v)
        list_comp.append(v)

4it [00:02,  2.12it/s]

3 269940


12it [00:07,  1.61it/s]


In [26]:
report_2020[report_2020.corp_code.isin(list_comp)]

corp_code corp_name stock_code corp_cls              report_nm  \
1142    269940      하나투어     039130        Y  [기재정정]사업보고서 (2020.12)   

            rcept_no flr_nm  rcept_dt rm    name_code  
1142  20210329000797   하나투어  20210329  연  하나투어_269940

In [27]:
dart.document('20210329000797')

UnicodeDecodeError: 'utf-8' codec can't decode byte 0xbb in position 214: invalid start byte

In [31]:
hana = dart.list('하나투어',start = '2021-01-01', end = '2022-03-17', kind='A', final= False)

In [35]:
hana[hana['report_nm'].str.contains(r'사업보고서(.)*(2020.12)')]

corp_code corp_name stock_code corp_cls              report_nm  \
5  00269940      하나투어     039130        Y  [기재정정]사업보고서 (2020.12)   
6  00269940      하나투어     039130        Y        사업보고서 (2020.12)   

         rcept_no flr_nm  rcept_dt  rm  
5  20210329000797   하나투어  20210329   연  
6  20210318001157   하나투어  20210318  정연

In [39]:
# 하나투어 처리 
xml_text = dart.document('20210318001157')
with open('report_2020.txt', 'a') as f:
    f.write('00269940') 
    f.write('\t')
    f.write(preprocessing(xml_text))
    f.write('\n')